In [2]:
import pandas as pd
import networkx as nx
import numpy as np
import folium

## Here

In [13]:
df = pd.read_csv('data/processed/Vacancy_new.csv', index_col=0, parse_dates = [2, 3, 4])

df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2629456 entries, 0 to 2629455
Data columns (total 13 columns):
 #   Column               Dtype         
---  ------               -----         
 0   car                  object        
 1   park_time            datetime64[ns]
 2   reservation_time     datetime64[ns]
 3   start_time           datetime64[ns]
 4   time_to_reservation  float64       
 5   time_to_start        float64       
 6   park_location_lat    float64       
 7   park_location_long   float64       
 8   park_zone            int64         
 9   park_fuel            int64         
 10  leave_fuel           int64         
 11  engine               object        
 12  moved                float64       
dtypes: datetime64[ns](3), float64(5), int64(3), object(2)
memory usage: 280.9+ MB


In [14]:
def haversine_alt(df, car1, car2):
    dfc1 = df[df.car == car1]
    dfc2 = df[df.car == car2]

    point1 = dfc1[['park_location_lat','park_location_long']].values[0]
    point2 = dfc2[['park_location_lat','park_location_long']].values[0]
    #return point1

    # convert decimal degrees to radians
    lat1, lon1 = map(np.radians, point1)
    lat2, lon2 = map(np.radians, point2)

    # Deltas
    delta_lon = lon2 - lon1 
    delta_lat = lat2 - lat1 
    
    # haversine formula 
    a = np.sin(delta_lat/2)**2 + np.cos(lat1) * np.cos(lat2) * np.sin(delta_lon/2)**2
    c = 2 * np.arcsin(np.sqrt(a)) 
    r = 6371000 # Radius of earth in m
    return c * r

In [24]:
sub_df

car           park_time    reservation_time  \
3438     WBY1Z21010V307859 2018-01-25 07:49:01 2018-01-25 09:31:24   
4253     WBY1Z21010V307859 2018-01-08 00:15:19 2018-08-01 15:34:49   
9113     WBY1Z21080V307941 2018-01-04 10:02:40 2018-04-01 06:02:08   
9250     WBY1Z21080V307941 2018-01-05 00:06:00 2018-05-01 09:36:24   
9407     WBY1Z21080V307941 2018-01-06 03:31:56 2018-05-31 03:03:21   
...                    ...                 ...                 ...   
2249846  WMWXR3109KTK68709 2018-01-12 00:22:03 2018-12-07 22:39:00   
2251888  WBA1R5105J7B14249 2018-01-12 21:15:59 2018-02-08 14:08:50   
2252171  WBA1R5105J7B14249 2018-01-08 18:13:06 2018-08-09 04:20:36   
2252589  WBA1R5105J7B14249 2018-01-12 01:33:09 2018-12-07 19:25:31   
2254771  WMWXU7109KTM90592 2018-01-12 18:03:44 2018-02-07 20:52:46   

                 start_time  time_to_reservation  time_to_start  \
3438    2018-01-25 09:40:24             1.706389       1.856389   
4253    2018-08-01 15:40:49          4935.325000    4935.425000   
9113    2018-04-01 06:11:08          2083.991111    2084.141111   
9250    2018-05-01 09:43:24          2793.506667    2793.623333   
9407    2018-05-31 03:04:21          3479.523611    3479.540278   
...                     ...                  ...            ...   
2249846 2018-12-07 22:51:00          7918.282500    7918.482500   
2251888 2018-02-08 14:24:50           640.880833     641.147500   
2252171 2018-08-09 04:29:36          5098.125000    5098.275000   
2252589 2018-12-07 19:51:31          7913.872778    7914.306111   
2254771 2018-02-07 20:58:46           626.817222     626.917222   

         park_location_lat  park_location_long  park_zone  park_fuel  \
3438             55.705247           12.561275     102423         84   
4253             55.714116           12.571873     102324         63   
9113             55.654502           12.540077     102852          0   
9250             55.688468           12.588897     102212         38   
9407              0.000000            0.000000     550062          0   
...                    ...                 ...        ...        ...   
2249846          55.681686           12.569719     102142         37   
2251888          55.687682           12.596271     102221         82   
2252171          55.630674           12.649027     185203         48   
2252589          55.711896           12.535409     102532         23   
2254771          55.730951           12.396868     151021         40   

         leave_fuel  engine         moved  
3438             84      I3  0.000000e+00  
4253             52      I3  7.805101e+03  
9113             68      I3  6.293673e+03  
9250             13      I3  7.467732e+03  
9407             37      I3  6.295673e+06  
...             ...     ...           ...  
2249846          36  COOPER  1.167621e+04  
2251888          96    118I  7.031517e+03  
2252171          34    118I  7.582550e+03  
2252589          80    118I  8.298767e+03  
2254771          27  COOPER  7.334981e+03  

[1417 rows x 13 columns]

In [23]:
timestamp = np.datetime64('2018-01-25T08:30:30')
sub_df = df[(df.park_time < timestamp) & (df.start_time > timestamp)]
sub_df.describe()

time_to_reservation  time_to_start  park_location_lat  \
count          1417.000000    1417.000000        1417.000000   
mean           3354.109650    3354.669954          54.896303   
std            2866.521430    2866.453801           6.570812   
min               0.001944       0.195556           0.000000   
25%             609.067778     609.170278          55.660258   
50%            2807.925278    2808.125278          55.679288   
75%            5783.209444    5783.442778          55.705169   
max            7930.194722    7930.511389          55.997541   

       park_location_long      park_zone    park_fuel   leave_fuel  \
count         1417.000000    1417.000000  1417.000000  1417.000000   
mean            12.369835  122808.171489    64.344390    63.988003   
std              1.481777   57099.718720    28.996419    28.894103   
min              0.000000  102111.000000     0.000000    -1.000000   
25%             12.519109  102445.000000    41.000000    42.000000   
50%             12.550698  102822.000000    67.000000    67.000000   
75%             12.582183  147112.000000    93.000000    92.000000   
max             12.676094  550062.000000   100.000000   100.000000   

              moved  
count  1.417000e+03  
mean   1.717236e+05  
std    1.003332e+06  
min    0.000000e+00  
25%    1.085572e+03  
50%    4.177940e+03  
75%    7.611578e+03  
max    6.328536e+06

In [15]:
def make_graph(df, timestamp, max_dist):
    def _edge_weight(x, max_dist):
        return max((max_dist-x)/max_dist,0)
    sub_df = df[(df.park_time < timestamp) & (df.reservation_time > timestamp)]
    sub_df = sub_df.assign(movedTF = (sub_df.moved > 100).astype(int))
    A = pd.DataFrame(data = [[_edge_weight(haversine_alt(sub_df, car1, car2), max_dist) for car1 in sub_df.car] for car2 in sub_df.car], index = sub_df.car, columns=sub_df.car)
    G = nx.from_pandas_adjacency(A)
    nx.set_node_attributes(G, sub_df.set_index('car').to_dict('index'))
    return G

In [16]:
timestamp = np.datetime64('2018-01-25T08:30:30')
#sub_df = df[(df.park_time < timestamp) & (df.reservation_time > timestamp)] # This is done twice
G = make_graph(df, timestamp, 1500)

NetworkXError: Adjacency matrix not square: nx,ny=(1384, 4554)

In [ ]:
node_attr = pd.DataFrame.from_dict(dict(G.nodes(data=True)), orient='index')
locations = {i: (r['park_location_lat'],r['park_location_long']) for i, r in node_attr.iterrows()}

A_flatten = pd.melt(nx.to_pandas_adjacency(G), ignore_index=False,var_name='car2', value_name='Weight').rename_axis("car1").reset_index()
A_flatten = A_flatten[A_flatten.Weight > 0]
A_flatten['car1'] = A_flatten['car1'].map(locations)
A_flatten['car2'] = A_flatten['car2'].map(locations)
A_flatten

car1                    car2    Weight
0      (55.783388, 12.517983)  (55.783388, 12.517983)  1.000000
40     (55.782498, 12.519595)  (55.783388, 12.517983)  0.905829
45     (55.779343, 12.519487)  (55.783388, 12.517983)  0.693660
54     (55.782374, 12.519525)  (55.783388, 12.517983)  0.901096
59     (55.769989, 12.516403)  (55.783388, 12.517983)  0.004551
...                       ...                     ...       ...
84310    (55.59233, 12.67601)  (55.585996, 12.658314)  0.122482
84388  (55.585996, 12.658314)  (55.585996, 12.658314)  1.000000
84575  (55.731345, 12.445186)  (55.733271, 12.444918)  0.856788
84591  (55.732392, 12.440973)  (55.733271, 12.444918)  0.822915
84680  (55.733271, 12.444918)  (55.733271, 12.444918)  1.000000

[4837 rows x 3 columns]

In [ ]:
# Function to add a point to the map
def plot_cars(map, latitude, longitude, col = 4, tooltip = None):
    for lat, lon, c, tt in zip(latitude, longitude, col, tooltip):
        folium.CircleMarker(location=[lat, lon],
                                tooltip = tt,
                                radius=1.5,
                                weight=4,
                                color = c).add_to(map)

# Function to add edges
def plot_edges(map, edge_df):
    for _, r in edge_df.iterrows():
        folium.PolyLine([r['car1'],r['car2']],
                    color='black',
                    weight=1,
                    opacity=r['Weight']).add_to(map)

# Initialize map
m = folium.Map(location=[55.69, 12.568337], zoom_start=12, prefer_canvas=True)

# Add points
plot_cars(m, node_attr['park_location_lat'], node_attr['park_location_long'], node_attr.replace({"movedTF": {0: 'Red', 1: 'Blue'}})['movedTF'],  node_attr.index)# + "<br>" + node_attr['park_battery'])

plot_edges(m, A_flatten)

# Show map
m

In [10]:
# Function to add a point to the map
def plot_cars(map, latitude, longitude, col = 4, tooltip = None):
    for lat, lon, c, tt in zip(latitude, longitude, col, tooltip):
        folium.CircleMarker(location=[lat, lon],
                                tooltip = tt,
                                radius=1.5,
                                weight=4,
                                color = c).add_to(map)

# Function to add edges
def plot_edges(map, edge_df):
    for _, r in edge_df.iterrows():
        folium.PolyLine([r['car1'],r['car2']],
                    color='black',
                    weight=1,
                    opacity=r['Weight']).add_to(map)

# Initialize map
m = folium.Map(location=[55.69, 12.568337], zoom_start=12, prefer_canvas=True)

# Add points
plot_cars(m, node_attr['park_location_lat'], node_attr['park_location_long'], node_attr.replace({"movedTF": {0: 'Red', 1: 'Blue'}})['movedTF'],  node_attr.index)# + "<br>" + node_attr['park_battery'])

plot_edges(m, A_flatten)

# Show map
m

In [1]:
1+1

2